In [2]:
import requests

auth_url = "https://signin.tradestation.com/authorize"

public_key = "r4bJ08Nbz9f8b6djDhoyCmazNnrrLFL4"
private_key = "hFBk8xgV_UGJEUFnxVW-AFz6YToqZwdvM-48x5wLUQhzKiR99r2w780hL0giBfvd"

params = {"response_type": "code", "client_id": public_key, "redirect_uri": "http://localhost", "audience": "https://api.tradestation.com", "state": "STATE", 
        "scope": "openid offline_access profile MarketData ReadAccount Trade Crypto Matrix OptionSpreads"}

response = requests.get(auth_url, params=params)
response.history
for resp in response.history:
        print(resp.status_code, resp.url)

302 https://signin.tradestation.com/authorize?response_type=code&client_id=r4bJ08Nbz9f8b6djDhoyCmazNnrrLFL4&redirect_uri=http%3A%2F%2Flocalhost&audience=https%3A%2F%2Fapi.tradestation.com&state=STATE&scope=openid+offline_access+profile+MarketData+ReadAccount+Trade+Crypto+Matrix+OptionSpreads


In [10]:
import requests

token_url = "https://signin.tradestation.com/oauth/token"

authorization_code = "xxMZvFaqtX95pCIj"

headers = {"content-type": "application/x-www-form-urlencoded"}
data = {"grant_type": "authorization_code", "client_id": public_key, "client_secret": private_key, "code": authorization_code, "redirect_uri": "http://localhost"}

r = requests.post(token_url, headers=headers, data=data).json()
print(r)

access_token = r["access_token"]
refresh_token = r["refresh_token"]
id_token = r["id_token"]

{'access_token': 'eyJhbGciOiJSUzI1NiIsInR5cCI6IkpXVCIsImtpZCI6Ik56WXpOekExUXpORVJFTXpNMFZHTkVSRVFqSTBSakV4TmpZek56aEdRVFJETmtJd1JVVXpNUSJ9.eyJodHRwOi8vdHJhZGVzdGF0aW9uLmNvbS9pZ25vcmVfZHVhbF9sb2dvbiI6ImZhbHNlIiwiaHR0cDovL3RyYWRlc3RhdGlvbi5jb20vY2xpZW50X3RhZyI6IlFnbm4yIiwiaHR0cDovL3RyYWRlc3RhdGlvbi5jb20vdXNlcm5hbWUiOiJob25nemhvdTExMSIsImh0dHA6Ly90cmFkZXN0YXRpb24uY29tL2ZkY25faWQiOiIxMDQ2MTgwNyIsImh0dHA6Ly90cmFkZXN0YXRpb24uY29tL2NyeXB0b19pZCI6Ijk4OGQxMTE5LWQ0OTUtNDEwNS1hMDk2LWRiN2U1ZDY2ZTliNyIsImh0dHA6Ly90cmFkZXN0YXRpb24uY29tL29ueXhfaWQiOjQxMjE1OTMsImlzcyI6Imh0dHBzOi8vc2lnbmluLnRyYWRlc3RhdGlvbi5jb20vIiwic3ViIjoiYXV0aDB8MTA0NjE4MDciLCJhdWQiOlsiaHR0cHM6Ly9hcGkudHJhZGVzdGF0aW9uLmNvbSIsImh0dHBzOi8vdHJhZGVzdGF0aW9uLXByb2QudHNsb2dpbi5hdXRoMC5jb20vdXNlcmluZm8iXSwiaWF0IjoxNjg1NDU1MjU0LCJleHAiOjE2ODU0NTY0NTQsImF6cCI6InI0YkowOE5iejlmOGI2ZGpEaG95Q21hek5ucnJMRkw0Iiwic2NvcGUiOiJvcGVuaWQgcHJvZmlsZSBNYXJrZXREYXRhIFJlYWRBY2NvdW50IFRyYWRlIE1hdHJpeCBDcnlwdG8gT3B0aW9uU3ByZWFkcyBvZmZsaW5lX2FjY2VzcyJ9.nMDpNZzM

In [11]:
import requests

def refresh():
    token_url = "https://signin.tradestation.com/oauth/token"

    headers = {"content-type": "application/x-www-form-urlencoded"}
    data = {"grant_type": "refresh_token", "client_id": public_key, "client_secret": private_key, "refresh_token": refresh_token}

    r = requests.post(token_url, headers=headers, data=data).json()

    access_token = r["access_token"]
    return access_token

In [ ]:
import requests
import pandas as pd
import json
import csv

url = "https://api.tradestation.com/v3/marketdata/barcharts/TSLA"

headers = {"Authorization": f"Bearer {access_token}"}

params = {"unit": "Minute", "firstdate": "2016-12-05T21:00:00Z", "lastdate": "2016-12-06T21:00:00Z"}

response = requests.request("GET", url, headers=headers, stream=True, params=params)
print(response)
if response.status_code == 401:
    access_token = refresh()
    headers = {"Authorization": f"Bearer {access_token}"}
    response = requests.request("GET", url, headers=headers, stream=True, params=params)
    print(response)
response = response.json()
    
fieldnames = list(response["Bars"][0].keys())
with open("tradestation_data/tsla_2016_12_05_2016_12_06.csv", "w", newline="") as csvfile:
    writer = csv.DictWriter(csvfile, fieldnames=fieldnames)

    writer.writeheader()
    for row in response["Bars"]:
        writer.writerow(row)

In [ ]:
def stream_quotes(symbols, path):
    url = f"https://api.tradestation.com/v3/marketdata/stream/quotes/{symbols}"
    access_token = refresh()
    headers = {"Authorization": f"Bearer {access_token}"}

    response = requests.get(url, headers=headers, stream=True)

    fieldnames = ["Symbol", "Last", "Ask", "AskSize", "Bid", "BidSize", "Volume", "TradeTime"]
    with open(path, "a", newline="") as csvfile:
        writer = csv.DictWriter(csvfile, fieldnames=fieldnames, extrasaction="ignore")
        if os.path.getsize(path) == 0:
            writer.writeheader()
        for line in response.iter_lines():
            if line:
                row = json.loads(line)
                if "Heartbeat" not in row:
                    writer.writerow(row)
                    print(row)
symbols = "MSFT"
path = "tradestation_data/msft_2023_05_31_stream.csv"
stream_quotes(symbols, path)

In [ ]:
import os
import csv
import json
import pandas as pd
from datetime import datetime
def stream_marketdepth_quotes(symbols, path):
    url = f"https://api.tradestation.com/v3/marketdata/stream/marketdepth/quotes/{symbols}"
    access_token = refresh()
    headers = {"Authorization": f"Bearer {access_token}"}

    response = requests.get(url, headers=headers, stream=True)

    # need to fix
    fieldnames = ["TimeStamp", "Side", "Price", "Size", "OrderCount", "Name"]
    with open(path, "a", newline="") as csvfile:
        writer = csv.DictWriter(csvfile, fieldnames=fieldnames, extrasaction="ignore")
        if not os.path.isfile(path):
            writer.writeheader()
        for line in response.iter_lines():
            if line:
                bids_and_asks = json.loads(line)
                if "Heartbeat" not in bids_and_asks:
                    for row in bids_and_asks["Bids"]:
                        writer.writerow(row)
                        print(row)
                    for row in bids_and_asks["Asks"]:
                        writer.writerow(row)
                        print(row)
            print(datetime.now())
                    
symbols = "GLDG"
path = "tradestation_data/gldg_2023_05_30_lvl2_stream.csv"
stream_marketdepth_quotes(symbols, path)

In [47]:
import requests
import time
import datetime
import pause
def get_quotes_10sec(symbols, path):
    next_time = datetime.datetime.now() + datetime.timedelta(0, 10)
    url = f"https://api.tradestation.com/v3/marketdata/quotes/{symbols}"
    while True:
        try:
            pause.until(next_time)
            access_token = refresh()
            headers = {"Authorization": f"Bearer {access_token}"}

            response = requests.get(url, headers=headers).json()
            print(response["Quotes"][0])
            fieldnames = ["Symbol", "Open", "High", "Low", "Last", "Ask", "AskSize", "Bid", "BidSize", "Volume", "TradeTime"]
            with open(path, "a", newline="") as csvfile:
                writer = csv.DictWriter(csvfile, fieldnames=fieldnames, extrasaction="ignore")
                if os.path.getsize(path) == 0:
                    writer.writeheader()
                writer.writerow(response["Quotes"][0])
                print(response)
                print(next_time)
                print(datetime.datetime.now())
            next_time += datetime.timedelta(0, 10)
        except requests.exceptions.ChunkedEncodingError as chunkError:
            print(chunkError)
            continue
        except Exception as e:
            print(e)
            break
symbols = "TSLA"
path = "tradestation_data/tsla_2023_05_31_10sec.csv"
get_quotes_10sec(symbols, path)

{'Symbol': 'TSLA', 'Open': '0', 'High': '0', 'Low': '0', 'PreviousClose': '201.16', 'Last': '199.36', 'Ask': '199.4', 'AskSize': '400', 'Bid': '199.35', 'BidSize': '200', 'NetChange': '-1.8', 'NetChangePct': '-0.894810101411812', 'High52Week': '314.66666', 'High52WeekTimestamp': '2022-08-16T00:00:00Z', 'Low52Week': '101.81', 'Low52WeekTimestamp': '2023-01-06T00:00:00Z', 'Volume': '118088', 'PreviousVolume': '128818746', 'Close': '201.16', 'DailyOpenInterest': '0', 'TradeTime': '2023-05-31T08:45:39Z', 'TickSizeTier': '0', 'MarketFlags': {'IsDelayed': False, 'IsHardToBorrow': False, 'IsBats': False, 'IsHalted': False}, 'LastSize': '100', 'LastVenue': 'EDGX', 'VWAP': '0'}
{'Quotes': [{'Symbol': 'TSLA', 'Open': '0', 'High': '0', 'Low': '0', 'PreviousClose': '201.16', 'Last': '199.36', 'Ask': '199.4', 'AskSize': '400', 'Bid': '199.35', 'BidSize': '200', 'NetChange': '-1.8', 'NetChangePct': '-0.894810101411812', 'High52Week': '314.66666', 'High52WeekTimestamp': '2022-08-16T00:00:00Z', 'Low52